In [1]:
import pandas as pd
import numpy as np

#Reading the 'plays' dataset, turning all items into integers
users = pd.DataFrame(np.array([i.strip().split("\t") for i in open('lastfm_data/user_artists.dat', 'r', encoding='latin-1').readlines()]),
                       columns = ['userID', 'artistID', 'plays'])
users = users.drop(users.index[0])
users = users.apply(pd.to_numeric)
users.head()

#Reading 'artists' dataset, splitting the first column into three columns on the newline, turning artistid into int
artists = pd.DataFrame(open('lastfm_data/artists.dat', 'r',  encoding='latin-1').readlines())
artists = pd.DataFrame(artists[0].str.split("\t").values.tolist(),columns = ['artistID', 'name', 'url', 'pictureURL'])
artists = artists.drop(artists.index[0])
artists['artistID'] = artists['artistID'].apply(pd.to_numeric)
artists = artists.drop(columns = ['url', 'pictureURL'])

In [2]:
artists.head()

artistID               name
1         1       MALICE MIZER
2         2    Diary of Dreams
3         3  Carpathian Forest
4         4       Moi dix Mois
5         5        Bella Morte

In [3]:
A = users.pivot(index = 'userID', columns ='artistID', values = 'plays').fillna(0)

In [4]:
A_vals = A.values
ratings_mean = np.mean(A_vals, axis = 1)
A_norm = A_vals - ratings_mean.reshape(-1, 1)
A_norm[:10]

array([[-9.56992967, -9.56992967, -9.56992967, ..., -9.56992967,
        -9.56992967, -9.56992967],
       [-1.16271552, -1.16271552, -1.16271552, ..., -1.16271552,
        -1.16271552, -1.16271552],
       [-1.52733666, -1.52733666, -1.52733666, ..., -1.52733666,
        -1.52733666, -1.52733666],
       ...,
       [-1.45173548, -1.45173548, -1.45173548, ..., -1.45173548,
        -1.45173548, -1.45173548],
       [-1.61768376, -1.61768376, -1.61768376, ..., -1.61768376,
        -1.61768376, -1.61768376],
       [-2.43421053, -2.43421053, -2.43421053, ..., -2.43421053,
        -2.43421053, -2.43421053]])

In [ ]:
from scipy.sparse.linalg import svds
U, sigma, Vt = svds(A_norm, k = 50)

In [ ]:
print(sigma, sigma.shape)
sigma = np.diag(sigma)
sigma, sigma.shape

In [ ]:
predictions = np.dot(np.dot(U, sigma), Vt) + ratings_mean.reshape(-1, 1)

In [ ]:
predictions_df = pd.DataFrame(predictions, columns = A.columns)

In [ ]:
predictions_df.iloc[99]

In [ ]:
def recommender(predictions_df, UID, movies_df, original_ratings_df, num_recommendations=5):
    
    # Get and sort the user's predictions
    user_row = UID - 1 # UID starts at 1, not 0
    sorted_predictions = predictions_df.iloc[user_row].sort_values(ascending=False) 
    
    # Get the original user data and merge in the movie information 
    user_data = original_ratings_df[original_ratings_df.userID == (UID)]
    user_full = user_data.merge(movies_df, how = 'left', left_on = 'artistID', right_on = 'artistID').sort_values(['plays'], ascending=False)

    
    # Recommend the highest predicted rating movies that the user hasn't seen yet.
    recommendations = movies_df[~movies_df['artistID'].isin(user_full['artistID'])] \
                      .merge(pd.DataFrame(sorted_predictions).reset_index(), 
                             how = 'left', left_on = 'artistID', right_on = 'artistID') \
                      .rename(columns = {user_row: 'Predictions'}) \
                      .sort_values('Predictions', ascending = False) \
                      .iloc[:num_recommendations, :-1]
                    
    print ('User {0} has already rated {1} movies.'.format(UID, user_full.shape[0]))
    print ('Recommending highest {0} predicted ratings movies not already rated.'.format(num_recommendations))
    return user_full, recommendations

In [ ]:
recommender(predictions_df, 500, artists, users, num_recommendations=5)

In [5]:
from sklearn.metrics.pairwise import cosine_similarity, euclidean_distances
from sklearn.neighbors import NearestNeighbors

In [6]:
users_artists = pd.merge(artists, users, on='artistID', how='left')

In [7]:
users_artists.head()

artistID             name  userID  plays
0         1     MALICE MIZER      34    212
1         1     MALICE MIZER     274    483
2         1     MALICE MIZER     785     76
3         2  Diary of Dreams     135   1021
4         2  Diary of Dreams     257    152

In [8]:
pivot_data = users_artists.pivot(index = 'userID', columns = 'name', values = 'plays').fillna(0)

In [9]:
pivot_data.head()

name    !!!  !DISTAIN  !deladap  "Weird Al" Yankovic  #####  #2 Orchestra  \
userID                                                                      
2       0.0       0.0       0.0                  0.0    0.0           0.0   
3       0.0       0.0       0.0                  0.0    0.0           0.0   
4       0.0       0.0       0.0                  0.0    0.0           0.0   
5       0.0       0.0       0.0                  0.0    0.0           0.0   
6       0.0       0.0       0.0                  0.0    0.0           0.0   

name    $lick  $lick feat. Six-Fo  (1962-1966)  (Pre) Kingdom  \
userID                                                          
2         0.0                 0.0          0.0            0.0   
3         0.0                 0.0          0.0            0.0   
4         0.0                 0.0          0.0            0.0   
5         0.0                 0.0          0.0            0.0   
6         0.0                 0.0          0.0            0.0   

name            ...            í°ìë¼  íì  ï¼¬ï½ï¼¬ï½  \
userID          ...                                              
2               ...                  0.0     0.0           0.0   
3               ...                  0.0     0.0           0.0   
4               ...                  0.0     0.0           0.0   
5               ...                  0.0     0.0           0.0   
6               ...                  0.0     0.0           0.0   

name    ï¼­ï¼¡ï¼®ï¼®ï¼¥ï¼±ï¼µï¼©ï¼®  ï¼°ï¼¥ï¼²ï¼¥ï¼³ï¼´ï¼²ï¼¯ï¼©ï¼«ï¼¡  \
userID                                                                   
2                               0.0                                0.0   
3                               0.0                                0.0   
4                               0.0                                0.0   
5                               0.0                                0.0   
6                               0.0                                0.0   

name    ï¼²ï¼¥ï¼¤  ï¼¶ï½ï½ï½
ï½ï½ï¼¡  ï½ï½ï½ï½ï½ï½
ï½ï½ï½  \
userID                                                                  
2             0.0                    0.0                          0.0   
3             0.0                    0.0                          0.0   
4             0.0                    0.0                          0.0   
5             0.0                    0.0                          0.0   
6             0.0                    0.0                          0.0   

name    ï½ï½ï½ï½  ï½ï½ï½ï½ï½ï½ï½
  
userID                                       
2                0.0                    0.0  
3                0.0                    0.0  
4                0.0                    0.0  
5                0.0                    0.0  
6                0.0                    0.0  

[5 rows x 17632 columns]

In [ ]:
pivot_data.loc[pivot_data['Lady Gaga'] > 1]

In [ ]:
player_counts = pivot_data.sum(axis =0, skipna = True).sort_values(ascending=False)

In [ ]:
player_counts

In [10]:
pivot_data[pivot_data >= 1] = 1

In [ ]:
player_counts = pivot_data.sum(axis =0, skipna = True).sort_values(ascending=False)

In [ ]:
pivot_data['Lady Gaga'].unique()

In [ ]:
pivot_data

In [11]:
df = pivot_data.reset_index(drop=True)

In [ ]:
songs = pd.DataFrame(pivot_data.columns)

In [12]:
distance_matrix = cosine_similarity(df.T)
distance_matrix.shape

(17632, 17632)

In [15]:
distDF = pd.DataFrame(distance_matrix, columns=(df.columns), index=(df.columns))
distDF.shape[0]

17632

In [16]:
distDF

name                                          !!!  !DISTAIN  !deladap  \
name                                                                    
!!!                                           1.0       0.0       0.0   
!DISTAIN                                      0.0       1.0       0.0   
!deladap                                      0.0       0.0       1.0   
"Weird Al" Yankovic                           0.0       0.0       0.0   
#####                                         0.0       0.0       0.0   
#2 Orchestra                                  0.0       0.0       0.0   
$lick                                         0.0       0.0       0.0   
$lick feat. Six-Fo                            0.0       0.0       0.0   
(1962-1966)                                   0.0       0.0       0.0   
(Pre) Kingdom                                 0.0       0.0       0.0   
(We Are) Performance                          0.0       0.0       0.0   
(hed) Planet Earth                            0.0       0.0       0.0   
(sic)monic                                    0.0       0.0       0.0   
*NSYNC                                        0.0       0.0       0.0   
+44                                           0.0       0.0       0.0   
+\-                                           0.0       0.0       0.0   
-123 min.                                     0.0       0.0       0.0   
-OZ-                                          0.0       0.0       0.0   
-t de sangre                                  0.0       0.0       0.0   
...And The Earth Swarmed With Them            0.0       0.0       0.0   
...And You Will Know Us by the Trail of Dead  0.0       0.0       0.0   
.38 Special                                   0.0       0.0       0.0   
.crrust                                       0.0       0.0       0.0   
06 Children Of The Cross                      0.0       0.0       0.0   
08001                                         0.0       0.0       0.0   
1-800-ZOMBIE                                  0.0       0.0       0.0   
10 Years                                      0.0       0.0       0.0   
10-20 ÐÐÐ ÐÐ«Ð¥ÐÐÐÐ«Ð¥                 0.0       0.0       0.0   
100 Bitches                                   0.0       0.0       0.0   
1000names                                     0.0       0.0       0.0   
...                                           ...       ...       ...   
ìë
ìë ï¼ 2PM                          0.0       0.0       0.0   
ìë´ë¹                                     0.0       0.0       0.0   
ì¡ì§ì                                     0.0       0.0       0.0   
ì¹ë¦¬                                        0.0       0.0       0.0   
ìí¬ë¦¿                                     0.0       0.0       0.0   
ì í                                        0.0       0.0       0.0   
ììì¬ì´ë                               0.0       0.0       0.0   
ìì´ë¹                                     0.0       0.0       0.0   
ì íí° ì¤ì¿¨(After School)                0.0       0.0       0.0   
ì ë¸ë(MBLAQ)                              0.0       0.0       0.0   
ìëê±¸ì¤                                  0.0       0.0       0.0   
ì¤í                                        0.0       0.0       0.0   
ì´ë°ì¬                                     0.0       0.0       0.0   
ì´ìì(ì¬)                                0.0       0.0       0.0   
ì´ìì(ì¬);                               0.0       0.0       0.0   
ì´ì í                                     0.0       0.0       0.0   
ì´í¨ë¦¬                                     0.0       0.0       0.0   
ì¥ê·¼ì                                     0.0       0.0       0.0   
ì ë¹µì                                     0.0       0.0       0.0   
íì                                        0.0       0.0       0.0   
í°ìë¼                                     0.0       0.0       0.0   
íì                                        0.0       0.

In [17]:
gaga = pd.DataFrame(distDF['Lady Gaga'].sort_values(ascending=False)[0:11])

In [18]:
gaga

name       Lady Gaga  Britney Spears   Rihanna  Katy Perry  \
Lady Gaga        1.0        0.772024  0.761302    0.736621   

name       Christina Aguilera  BeyoncÃ©     Ke$ha   Madonna  Black Eyed Peas  \
Lady Gaga            0.691833  0.686279  0.659154  0.605498         0.600956   

name        Shakira  Avril Lavigne  
Lady Gaga  0.593452       0.592356

In [21]:
nice = pd.DataFrame({gaga.index.values[0] : list(gaga.columns[:])})

In [22]:
gagat = nice.T

In [23]:
gagat

0               1        2           3                   4   \
Lady Gaga  Lady Gaga  Britney Spears  Rihanna  Katy Perry  Christina Aguilera   

                 5      6        7                8        9              10  
Lady Gaga  BeyoncÃ©  Ke$ha  Madonna  Black Eyed Peas  Shakira  Avril Lavigne

In [24]:
timbaland = pd.DataFrame(distDF['Timbaland'].sort_values(ascending=False)[0:11]).T

In [25]:
nice2 = pd.DataFrame({timbaland.index.values[0] : list(timbaland.columns[:])})

In [26]:
nice3 = nice2.T

In [43]:
hello = distDF[:1].map(lambda x: x.sort_values(ascending=False)[0:11].T in distDF[x])

AttributeError: 'DataFrame' object has no attribute 'map'

In [27]:
gagat.append(nice3)

0               1                   2                3   \
Lady Gaga  Lady Gaga  Britney Spears             Rihanna       Katy Perry   
Timbaland  Timbaland         Rihanna  The Pussycat Dolls  Black Eyed Peas   

                           4         5                  6               7   \
Lady Gaga  Christina Aguilera  BeyoncÃ©              Ke$ha         Madonna   
Timbaland        David Guetta  BeyoncÃ©  Justin Timberlake  Britney Spears   

                        8              9                   10  
Lady Gaga  Black Eyed Peas        Shakira       Avril Lavigne  
Timbaland        Lady Gaga  Nelly Furtado  Christina Aguilera

In [34]:
# df = pd.DataFrame()
for x in fuck:
    gaga = pd.DataFrame(distDF[x].sort_values(ascending=False)[0:11])
    gagat = gaga.T
    print(gagat)
    
    
    

    nice = pd.DataFrame({gaga.index.values[0] : list(gaga.columns[:])})
#     nice2 = nice.T
#     print(nice2)
#     df.append(nice2)

name              Jay-Z & Coldplay  Fred Hammond & Radical for Christ  \
Jay-Z & Coldplay               1.0                           0.707107   

name              Big Mike  Mindthings     4chan  Mick Boogie & Terry Urban  \
Jay-Z & Coldplay  0.707107    0.707107  0.707107                   0.707107   

name              Square Enix  Rick GhraphiXxX  DJ Screw  Black&Mouse  \
Jay-Z & Coldplay     0.707107         0.707107  0.707107     0.707107   

name              Zion y Lennox  
Jay-Z & Coldplay       0.707107  
name                   Jay-Z and Linkin Park  ANNA inspi NANA      DCUP  \
Jay-Z and Linkin Park                    1.0         0.333333  0.333333   

name                         D2  Chris Willis  Brendon Urie and Dresden Dolls  \
Jay-Z and Linkin Park  0.333333      0.333333                        0.333333   

name                   Brendon Urie  Big Sean  \
Jay-Z and Linkin Park      0.333333  0.333333   

name                   PISTA SERTANEJA REMIXES   d-_-b  S Club 8  

name              Jedi Mind Tricks     Elzhi  The Alchemist  Hieroglyphics  \
Jedi Mind Tricks               1.0  0.471405       0.471405       0.471405   

name                    AZ  GZA/Genius  Jurassic 5     Big L   Raekwon  \
Jedi Mind Tricks  0.447214    0.421637    0.408248  0.408248  0.402015   

name              Black Milk  Kool G Rap  
Jedi Mind Tricks      0.3849      0.3849  
name     Jedward  Jessica Mauboy  Andrew Lawson     Sibel  ÐÐ°Ð¼Ð°  \
Jedward      1.0        0.707107       0.707107  0.707107  0.707107   

name     Amanda Lepore  ÐÐ¼Ð¸ÑÑÐ¸Ð¹ ÐÐ¾Ð»Ð´ÑÐ½  Gjoko Taneski  \
Jedward       0.707107                     0.707107       0.707107   

name     ÐÑÐ¸ÑÑÑÐºÐ°  Linda Teodosiu  Despina Vandi  
Jedward          0.707107        0.707107       0.707107  
name       Jeff Beck  Roy Buchanan  John Mayall & The Bluesbreakers  \
Jeff Beck        1.0      0.566947                         0.566947   

name       Jonny Lang  Canned Heat  Johnny Winter  Gary Moore  

name         Seven Percent Solution  The Vera Violets  æ²³æéä¸  \
Jeniferever                     1.0               1.0           1.0   

name         Jeniferever  Euphoria  The Telescopes  sleepy.ab  fathom 5  \
Jeniferever          1.0       1.0             1.0        1.0       1.0   

name         æé»  ë¯¸ì¸ë(ç¾äººå)  æ¾ããå­  
Jeniferever     1.0                   1.0           1.0  
name             Asher Book  Garrett Hedlund  Kerry Muzzey  Kevin McHale  \
Jenna Ushkowitz         1.0              1.0           1.0           1.0   

name             Jayma Mays  Amber Riley  Garrett Hedlund & Leighton Meester  \
Jenna Ushkowitz         1.0          1.0                                 1.0   

name             Finn  Nikki Williams  Cory Monteith  Jenna Ushkowitz  
Jenna Ushkowitz   1.0             1.0            1.0              1.0  
name              Jennette McCurdy  Keke Palmer  Cast Of 'Camp Rock 2'  \
Jennette McCurdy               1.0      0.57735           

name                Jeremy Messersmith  Villagers        Du  \
Jeremy Messersmith                 1.0   0.816497  0.707107   

name                Sad Day For Puppets  The New Raemon  Crystal Fighters  \
Jeremy Messersmith             0.707107        0.707107          0.707107   

name                Bye Bye Bicycle  The Leisure Society  Bishop Morocco  \
Jeremy Messersmith         0.707107             0.707107        0.707107   

name                Jacob Golden   amatria  
Jeremy Messersmith      0.707107  0.707107  
name          Jeremy Soule  Yattering  Atlantis  Pitbulls In The Nursery  \
Jeremy Soule           1.0        0.5       0.5                      0.5   

name          Jimmy Barnes  Cold Chisel  \
Jeremy Soule           0.5          0.5   

name          Heroes Of Might & Magic III Soundtrack  Sonic Mayhem  Maigra  \
Jeremy Soule                                     0.5           0.5     0.5   

name          Gothic II Soundtrack  Derek Duke  
Jeremy Soule                 

name            Jessica Mauboy  Sibel  Linda Teodosiu  Andrew Lawson  \
Jessica Mauboy             1.0    1.0             1.0            1.0   

name            Gjoko Taneski  ÐÐ¼Ð¸ÑÑÐ¸Ð¹ ÐÐ¾Ð»Ð´ÑÐ½   Jedward  \
Jessica Mauboy            1.0                          1.0  0.707107   

name               Sandy  Declan Galbraith  Hanna Pakarinen  Anna David  
Jessica Mauboy  0.707107          0.707107         0.707107    0.707107  
name             Jessica Simpson  Ashlee Simpson  Hilary Duff  \
Jessica Simpson              1.0         0.37565        0.375   

name             Jesse McCartney  Jennifer Lopez  Leona Lewis  Mariah Carey  \
Jessica Simpson         0.357217        0.337211     0.335992       0.33013   

name             Lindsay Lohan  The Pussycat Dolls  Christina Aguilera  \
Jessica Simpson        0.32423            0.319372            0.315997   

name             Britney Spears  
Jessica Simpson        0.311853  
name           Jessica Sutta    Jessy  Rodrigo e RogÃ©r

...

name       ç§å·§é³  æ¥åå¬  S.H.E  ÐÐ°Ð»ÐµÑÐ¸Ð¹ ÐÐµÐ¾Ð½ÑÑÐµÐ²  \
æ¥åå¬        1.0        1.0    1.0                              1.0   

name       Alejandro Magno  ÐÑÐ°ÐºÐ»Ð¸  å¨è¯å¥  é³å¥è¿  è­äºè»  \
æ¥åå¬              1.0           1.0        1.0        1.0        1.0   

name       è«æè  Armik  
æ¥åå¬        1.0    1.0  
name    Suara  å·¥è¤éé¦  å½©é³  å½©è  å¤å·ãã¿  ë°ì í  Cocco  \
æ¨¹æµ·    1.0           1.0     1.0     1.0           1.0        1.0    1.0   

name    FictionJunction YUUKA  ã¹ã¬ã·ã«ãª  æ æã¿ãªå®  \
æ¨¹æµ·                    1.0              1.0              1.0   

name    ä½è¤ã²ãç¾  
æ¨¹æµ·              1.0  
name          æ°´æ¨¹å¥ã    Buono!  èåå®é  HINOIãã¼ã   \
æ°´æ¨¹å¥ã           1.0  0.816497      0.816497        0.816497   

name          Aira Mitsuki    misono  Julma-Henri & SyrjÃ¤ytyneet  \
æ°´æ¨¹å¥ã      0.666667  0.666667                      0.57735   

name    

name       æ»æ²¢ç§æ  ä»äºç¿¼  Anahi  ã¿ãã­ã¼ï¼ç¿¼  ç¾å¿ç¥¥  \
ç¾å¿ç¥¥           1.0        1.0    1.0                 1.0        1.0   

name         ì¹ë¦¬       ë¹  æ±æ¹ç¥èµ·      AAA      JYJ  Patrick Nuo  
ç¾å¿ç¥¥  0.707107  0.707107       0.57735  0.57735  0.57735          0.5  
name       ç¦äºè  ãã­ã¼ï¼ãã­ã¸ã§ã¯ã  å æ±ç±è¡£  \
ç¾åä¼        1.0                             1.0           1.0   

name       ã¡ã­ã³è¨å¿µæ¥  ã­ã£ãã¡ã¼ãªå¶æ¥½é¨  ç¾åä¼  Miz  \
ç¾åä¼                 1.0                          1.0        1.0  1.0   

name       è¤æ¬ç¾è²´  See-Saw  ååºèå¥  å®åãªã¤ã¿  
ç¾åä¼           1.0      1.0           1.0              1.0  
name                                              Double Nation  DJ Remo  \
ç¾å°å¥³æ¦å£«ã»ã¼ã©ã¼ã ã¼ã³ã·ãªã¼ãº            1.0      1.0   

name                                              East West Rockerz  \
ç¾å°å¥³æ¦å£«ã»ã¼ã©ã¼ã ã¼ã³ã·

name             Giraffes? Giraffes!  OOIOO  Hifana  Zach Hill  \
é«åå¯ºç¾æ¯                  1.0    1.0     1.0        1.0   

name             Ahleuchatistas  Tony Trischka  Vincent Atmicus  ROVO  \
é«åå¯ºç¾æ¯             1.0            1.0              1.0   1.0   

name             Crime In Choir  Handsomeboy Technique  é«åå¯ºç¾æ¯  
é«åå¯ºç¾æ¯             1.0                    1.0              1.0  
name          Portishead + Epigones  kaman leung  é«æ©å¹¸å®  \
é«æ©å¹¸å®                    1.0          1.0           1.0   

name          totu 2009 DJ-Set all Songs not Mixed  Kruder & Dorfmeister  \
é«æ©å¹¸å®                                   1.0                   1.0   

name          é»æ°ã°ã«ã¼ã´  White Town  Jensemann  Jesus Jones  \
é«æ©å¹¸å®                 1.0         1.0        1.0     0.707107   

name          Cut Chemist  SLAPPER  
é«æ©å¹¸å®      0.57735      0.5  
name       ç¦äºè  ãã­ã¼ï¼ãã­ã¸ã§ã¯ã  å æ±ç±è¡£ 

name                  GRUPO 05  ìëìë ï¼ 2PM  Orange Caramel  \
ìëìë ï¼ 2PM       1.0                   1.0             1.0   

name                  Maite Perroni   Charice      Kara      f(x)  \
ìëìë ï¼ 2PM        0.57735  0.408248  0.377964  0.377964   

name                  Wonder Girls  We Are the Fallen    Lolene  \
ìëìë ï¼ 2PM      0.333333           0.333333  0.235702   

name                  Stone Temple Pilots  
ìëìë ï¼ 2PM             0.213201  
name       ìë´ë¹  Tha Blue Herb  YOU THE ROCKâ  TERIYAKI BOYZ   Tigarah  \
ìë´ë¹        1.0       0.707107         0.707107       0.707107  0.707107   

name       Rhymester  ì¡ì§ì  Mr.Children  ã±ãã¡ã¤ã·  \
ìë´ë¹   0.707107   0.707107     0.707107         0.707107   

name       KICK THE CAN CREW    ê°ì¸  
ìë´ë¹           0.707107  0.707107  
name       ê°ì¸  YOU THE ROCKâ  Dragon Ash  Tigarah  Mr.Children  \
ì¡ì§ì     1.0              1.0         1.

name          ï½ï½ï½ï½ï½ï½ï½  ãã¥ã¼ã³å·¥å ´  \
ï½ï½ï½ï½                    1.0                 1.0   

name          DOGinTheãã©ã¬ã«ã¯ã¼ã«ããªã¼ã±ã¹ãã©  \
ï½ï½ï½ï½                                                1.0    

name          ã¢ã³ããã  Dear Bitch  PENICILLIN  12012    D  Hi:BRiD  \
ï½ï½ï½ï½              1.0         1.0         1.0    1.0  1.0      1.0   

name          V-last.  ãã¦ãã¼  
ï½ï½ï½ï½      1.0           1.0  
name                   ï½ï½ï½ï½ï½ï½ï½  ãã¥ã¼ã³å·¥å ´  \
ï½ï½ï½ï½ï½ï½ï½                    1.0                 1.0   

name                   DOGinTheãã©ã¬ã«ã¯ã¼ã«ããªã¼ã±ã¹ãã©  \
ï½ï½ï½ï½ï½ï½ï½                                                1.0    

name                   ã¢ã³ããã  Dear Bitch  PENICILLIN  12012    D  \
ï½ï½ï½ï½ï½ï½ï½              1.0         1.0         1.0    1.0  1.0   

name                   Hi:BRiD  V-last.  ãã¦ãã¼  
ï½ï½

In [ ]:
for x in distDF:
    new_df = pd.DataFrame(distDF[x].sort_values(ascending=False)[0:11])
    new_df.T
    

In [ ]:
df

In [ ]:
new_df = distDF[:3]

In [ ]:
distDF[:3]

In [ ]:
# from sqlalchemy.orm import sessionmaker
# from sqlalchemy import create_engine

# engine = create_engine('sqlite://', echo=False)
# Session = sessionmaker(bind=engine)
# session = Session()
# pivot_data.to_sql('users', con=engine)

In [ ]:
model = NearestNeighbors(n_neighbors=distDF.shape[0])
model.fit(distDF)

In [ ]:
nearest_neighbours= model.kneighbors(distDF, return_distance=True)

In [ ]:
nearest_neighbours[1].shape

In [ ]:
NNDF = pd.DataFrame(distDF.columns[nearest_neighbours[1]], index=distDF.index)
top10=NNDF[NNDF.columns[1:11]]
top10

In [ ]:
df.shape

In [ ]:
model_knn = NearestNeighbors(n_neighbors=df.shape[0], metric='cosine', algorithm='brute')
model_knn.fit(df)

In [ ]:
nearest_neighbors= model_knn.kneighbors(df, return_distance=True)

In [ ]:
nn= pd.DataFrame(nearest_neighbors[1])
nn.head()

In [ ]:
query_index = np.random.choice(df.shape[0])
distance, indices = model_knn.kneighbors(df.iloc[query_index, :].reshape(-1), n_neighbors = 6)

In [ ]:
NNDF = pd.DataFrame(df.columns[nn], index=df.index)
top10=NNDF[df.columns[1:11]]
top10

In [ ]:
len(df.columns)

In [ ]:
len(nn)